# Tải thư viện

In [1]:
# !git clone https://github.com/cosmicman-cvpr2024/CosmicMan.git
# %cd CosmicMan

In [2]:
# Cập nhật pip và cài đặt các thư viện cần thiết
!pip install --upgrade pip
!pip install diffusers==0.30.0 safetensors sentencepiece transformers accelerate datasets bitsandbytes deepspeed gradio==3.48.0 pandas invisible-watermark
!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

!pip install --upgrade diffusers transformers accelerate
!pip install --upgrade peft

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 22.3 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 24.1.2
    Uninstalling pip-24.1.2:
      Successfully uninstalled pip-24.1.2
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 27.1 MB/s  0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of opencv-python to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 65.1 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.3/20.3 MB 135.5 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 86.4 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 566.1/566.1 kB 15.5 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.4/59.4 MB 117.5 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
import torch
from diffusers import StableDiffusionPipeline, UNet2DConditionModel, EulerDiscreteScheduler
from huggingface_hub import hf_hub_download
from safetensors.torch import load_file
from datasets import load_dataset
from PIL import Image
from tqdm import tqdm
import os
import glob

2025-11-08 06:05:45.725120: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1762581946.129607      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1762581946.258911      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


# Load model

In [4]:
base_path = "runwayml/stable-diffusion-v1-5"
unet_path = "cosmicman/CosmicMan-SD"

# Load model.
unet = UNet2DConditionModel.from_pretrained(unet_path, torch_dtype=torch.float16)
pipe = StableDiffusionPipeline.from_pretrained(base_path, unet=unet, torch_dtype=torch.float16, variant="fp16", safety_checker=None).to("cuda")
pipe.scheduler = EulerDiscreteScheduler.from_pretrained(base_path, subfolder="scheduler", torch_dtype=torch.float16)

config.json: 0.00B [00:00, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/3.44G [00:00<?, ?B/s]

The config attributes {'decay': 0.9999, 'inv_gamma': 1.0, 'min_decay': 0.0, 'optimization_step': 2000, 'power': 0.6666666666666666, 'update_after_step': 0, 'use_ema_warmup': False} were passed to UNet2DConditionModel, but are not expected and will be ignored. Please verify your config.json configuration file.


model_index.json:   0%|          | 0.00/541 [00:00<?, ?B/s]

Fetching 11 files:   0%|          | 0/11 [00:00<?, ?it/s]

...

config.json:   0%|          | 0.00/617 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/547 [00:00<?, ?B/s]

vae/diffusion_pytorch_model.fp16.safeten(…):   0%|          | 0.00/167M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

`torch_dtype` is deprecated! Use `dtype` instead!
You have disabled the safety checker for <class 'diffusers.pipelines.stable_diffusion.pipeline_stable_diffusion.StableDiffusionPipeline'> by passing `safety_checker=None`. Ensure that you abide to the conditions of the Stable Diffusion license and do not expose unfiltered results in services or applications open to the public. Both the diffusers team and Hugging Face strongly recommend to keep the safety filter enabled in all public facing circumstances, disabling it only for use-cases that involve analyzing network behavior or auditing its results. For more information, please have a look at https://github.com/huggingface/diffusers/pull/254 .


# Tạo ảnh 

## deepfashion-multimodal

In [5]:
# START_INDEX = 0
# END_INDEX = 1000
# IMAGE_SIZE = 1024
# REAL_DIR = "./real_images"
# GEN_DIR = "./generated_images"

# # Tạo các thư mục
# os.makedirs(REAL_DIR, exist_ok=True)
# os.makedirs(GEN_DIR, exist_ok=True)

# split_range = f'data[{START_INDEX}:{END_INDEX}]'

# # Tải 3000 mẫu đầu tiên từ split 'train'
# print(f"Đang tải các mẫu từ {START_INDEX} đến {END_INDEX} từ DeepFashion-MultiModal...")
# dataset = load_dataset(
#     "Marqo/deepfashion-multimodal",
#     split=split_range
# )

# print(f"Tải dữ liệu thành công. Bắt đầu xử lý {len(dataset)} ảnh.")

In [6]:
# num_steps = 30
# guidance_scale = 7.5

# print(f"Bắt đầu tạo {len(dataset)} ảnh. Quá trình này sẽ mất thời gian...")

# for i, example in enumerate(tqdm(dataset), start=START_INDEX):
#     try:
#         # --- 1. Xử lý và lưu ảnh thật ---
#         real_image = example['image'].convert("RGB")
#         real_image = real_image.resize((IMAGE_SIZE, IMAGE_SIZE), Image.LANCZOS)
#         real_image.save(os.path.join(REAL_DIR, f"{i:05d}.png"))

#         # --- 2. Lấy prompt và tạo ảnh ---
#         prompt = example['text']

#         # Tạo ảnh
#         gen_image = pipe(
#             prompt,
#             num_inference_steps=num_steps,
#             guidance_scale=guidance_scale,
#             height=IMAGE_SIZE,
#             width=IMAGE_SIZE
#         ).images[0]

#         # Lưu ảnh đã tạo
#         gen_image.save(os.path.join(GEN_DIR, f"{i:05d}.png"))

#     except Exception as e:
#         print(f"Lỗi ở ảnh {i}: {e}. Bỏ qua ảnh này.")

# print("Hoàn tất việc tạo ảnh!")

## mm-celeba-hq-dataset

In [7]:
START_INDEX = 0
END_INDEX = 500
IMAGE_SIZE = 1024
REAL_DIR = "./real_images"
GEN_DIR = "./generated_images"

# Tạo các thư mục (Không thay đổi)
os.makedirs(REAL_DIR, exist_ok=True)
os.makedirs(GEN_DIR, exist_ok=True)

In [8]:
IMAGE_DIR = "/kaggle/input/mm-celeba-hq-dataset/MM-CELEBA-HQ/images"
TEXT_DIR = "/kaggle/input/mm-celeba-hq-dataset/MM-CELEBA-HQ/text/celeba-caption"

print("Đang quét đường dẫn ảnh...")
# Lấy tất cả đường dẫn ảnh, giả sử là .jpg và sắp xếp lại
all_image_paths = sorted(glob.glob(os.path.join(IMAGE_DIR, "*.jpg")))

# Lấy các mẫu trong khoảng START_INDEX và END_INDEX
image_paths = all_image_paths[START_INDEX:END_INDEX]

print(f"Tải dữ liệu thành công. Bắt đầu xử lý {len(image_paths)} ảnh.")

Đang quét đường dẫn ảnh...
Tải dữ liệu thành công. Bắt đầu xử lý 500 ảnh.


In [9]:
num_steps = 30
guidance_scale = 7.5

print(f"Bắt đầu tạo {len(image_paths)} ảnh. Quá trình này sẽ mất thời gian...")

# Lặp qua danh sách đường dẫn ảnh thay vì dataset object
for i, image_path in enumerate(tqdm(image_paths), start=START_INDEX):
    try:
        # --- 1. Xử lý và lưu ảnh thật (Load từ path) ---
        real_image = Image.open(image_path).convert("RGB")
        real_image = real_image.resize((IMAGE_SIZE, IMAGE_SIZE), Image.LANCZOS)
        real_image.save(os.path.join(REAL_DIR, f"{i:05d}.png"))

        # --- 2. Lấy prompt ---
        
        # Lấy tên file ảnh (ví dụ: 00001.jpg)
        image_filename = os.path.basename(image_path)
        # Tạo tên file text tương ứng (ví dụ: 00001.txt)
        text_filename = os.path.splitext(image_filename)[0] + ".txt"
        # Tạo đường dẫn đầy đủ tới file text
        text_path = os.path.join(TEXT_DIR, text_filename)

        # Đọc tất cả các captions
        with open(text_path, 'r') as f:
            captions = [line.strip() for line in f.readlines() if line.strip()]

        # Chọn caption tốt nhất (dài nhất mà không quá 77 tokens)
        valid_captions = []
        for cap in captions:
            # Tokenize để kiểm tra độ dài. Dùng tokenizer của pipeline
            inputs = pipe.tokenizer(cap, return_tensors="pt", padding=False, truncation=False)
            token_count = inputs.input_ids.shape[1]
            
            # Giới hạn của CLIP là 77 tokens (bao gồm cả start/end tokens)
            if token_count <= 77:
                valid_captions.append(cap)
        
        if not valid_captions:
            # Nếu không có caption nào hợp lệ, gây lỗi để khối except bắt
            raise Exception(f"Không tìm thấy caption nào <= 77 tokens.")

        # Chọn caption dài nhất (đầy đủ ý nhất) trong số các caption hợp lệ
        prompt = max(valid_captions, key=len)


        # --- 3. Tạo ảnh ---
        gen_image = pipe(
            prompt,
            num_inference_steps=num_steps,
            guidance_scale=guidance_scale,
            height=IMAGE_SIZE,
            width=IMAGE_SIZE
        ).images[0]

        # Lưu ảnh đã tạo 
        gen_image.save(os.path.join(GEN_DIR, f"{i:05d}.png"))

    except Exception as e:
        # Thêm image_path vào log lỗi để dễ debug
        print(f"Lỗi ở ảnh {i} (path: {image_path}): {e}. Bỏ qua ảnh này.")

print("Hoàn tất việc tạo ảnh!")

Bắt đầu tạo 500 ảnh. Quá trình này sẽ mất thời gian...


  0%|          | 0/500 [00:00<?, ?it/s]

  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 1/500 [00:30<4:15:30, 30.72s/it]

  0%|          | 0/30 [00:00<?, ?it/s]

...

  0%|          | 0/30 [00:00<?, ?it/s]

100%|█████████▉| 499/500 [4:25:46<00:31, 31.95s/it]

  0%|          | 0/30 [00:00<?, ?it/s]

100%|██████████| 500/500 [4:26:18<00:00, 31.96s/it]

Hoàn tất việc tạo ảnh!
